In [26]:
# Import Libraries

import yfinance as yf
import pandas as pd
import numpy as np
import talib as ta

import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

Tickers

In [27]:
# Tickers List
TICKERS = ["V", "INTC", "CAT", "LLY", "DIS", "TSLA", "GS", "BA", "CSCO","ABBV",
          "AMZN", "JPM", "KO", "MCD", "PYPL", "WMT", "IBM", "AMGN", "REGN", "JNJ"]
TICKER = 'MSFT'
START = '2021-01-01'

In [28]:
ticker = yf.Ticker(TICKER)
df = ticker.history(start=START)[['Open', 'Close', 'High', 'Low', 'Volume']]
df

Open       Close        High         Low  \
Date                                                                        
2021-01-04 00:00:00-05:00  216.710072  211.996658  217.167781  209.191975   
2021-01-05 00:00:00-05:00  211.577895  212.201157  212.804952  210.058697   
2021-01-06 00:00:00-05:00  206.620989  206.698898  210.828012  206.397008   
2021-01-07 00:00:00-05:00  208.442070  212.580917  213.603459  208.120714   
2021-01-08 00:00:00-05:00  212.960726  213.876144  214.811044  211.353886   
...                               ...         ...         ...         ...   
2023-12-18 00:00:00-05:00  369.450012  372.649994  373.000000  368.679993   
2023-12-19 00:00:00-05:00  371.489990  373.260010  373.260010  369.839996   
2023-12-20 00:00:00-05:00  375.000000  370.619995  376.029999  370.529999   
2023-12-21 00:00:00-05:00  372.559998  373.540009  374.410004  370.040009   
2023-12-22 00:00:00-05:00  373.679993  374.579987  375.179993  372.709991   

                             Volume  
Date                                 
2021-01-04 00:00:00-05:00  37130100  
2021-01-05 00:00:00-05:00  23823000  
2021-01-06 00:00:00-05:00  35930700  
2021-01-07 00:00:00-05:00  27694500  
2021-01-08 00:00:00-05:00  22956200  
...                             ...  
2023-12-18 00:00:00-05:00  21802900  
2023-12-19 00:00:00-05:00  20603700  
2023-12-20 00:00:00-05:00  26316700  
2023-12-21 00:00:00-05:00  17708000  
2023-12-22 00:00:00-05:00  17091100  

[749 rows x 5 columns]

Graph Settings

In [29]:
TEMPLATE = 'plotly_dark'
def set_padding(fig):
    fig.update_layout(margin = go.layout.Margin(r=10,b=10))

def add_range_selector(fig):
    fig.update_layout(
        xaxis=dict(
            rangeselector=dict(
                buttons=[
                    dict(count=1, label='1m', step='month', stepmode='backward'),
                    dict(count=6, label='6m', step='month', stepmode='backward'),
                    dict(count=1, label='YTD', step='year', stepmode='todate'),
                    dict(count=1, label='1y', step='year', stepmode='backward'),
                    dict(step='all')
                ]),
            type='date'),
        xaxis2_type='date')


def add_volume_chart(fig):
    colors = ['#9C1F0B' if row['Open'] - row['Close'] >= 0
              else '#2B8308' for index, row in df.iterrows()]
    
    fig.add_trace(go.Bar(x=df.index, y=df['Volume'], showlegend = False, marker_color = colors), row = 2, col = 1)

Removing Empty Dates

In [30]:
dt_all = pd.date_range(start=df.index[0],end=df.index[-1])
dt_obs = [d.strftime("%y-%m-%d") for d in pd.to_datetime(df.index)]
dt_breaks = [d for d in dt_all.strftime("%y-%m-%d").tolist() if not d in dt_obs]

Plotting Price and Volume charts

In [31]:
fig1 = make_subplots(rows = 2, cols=1, vertical_spacing=0.01, shared_xaxes=True)
fig1.add_trace(go.Scatter(x=df.index, y=df['Close'], name='Price'))
add_volume_chart(fig1)
add_range_selector(fig1)
fig1.update_layout(xaxis=dict(rangeselector = dict(font = dict( color = 'black'))))
fig1.update_yaxes(title_text = 'Price', row = 1, col = 1)
fig1.update_yaxes(title_text = 'Volume', row =2, col = 1)
set_padding(fig1)
fig1.update_xaxes(rangebreaks=[dict(values=dt_breaks)])
layout1 = go.Layout(template=TEMPLATE, title=TICKER + ' - Price and Volume', height=500)
fig1.update_layout(layout1)

Plot Price, SMA and EMA charts

In [32]:
df['SMA'] = ta.SMA(df['Close'], timeperiod = 5)
df['EMA'] = ta.EMA(df['Close'], timeperiod = 5)

fig2 = make_subplots(rows=2,cols=1,vertical_spacing=0.01,shared_xaxes=True)
for col in ['Close', 'SMA', 'EMA']:
    fig2.add_trace(go.Scatter(x=df.index, y=df[col], name=col), row=1, col=1)

fig2.data[0].name = 'Price'
add_volume_chart(fig2)
add_range_selector(fig2)
fig2.update_layout(xaxis=dict(rangeselector = dict(font = dict( color = 'black'))))
fig2.update_yaxes(title_text = 'Price', row=1, col=1)
fig2.update_yaxes(title_text = 'Volume', row=2, col=1)
set_padding(fig2)
fig2.update_xaxes(rangebreaks=[dict(values=dt_breaks)])
layout2 = go.Layout(template=TEMPLATE, title=TICKER + ' - Price, SMA, EMA and Volume', height=500)
fig2.update_layout(layout2)

Plot Price, SMA-50 and SMA-200

In [33]:
df['SMA-50'] = ta.SMA(df['Close'], timeperiod = 50)
df['SMA-200'] = ta.SMA(df['Close'], timeperiod = 200)

fig3 = make_subplots(rows=2,cols=1,vertical_spacing=0.01,shared_xaxes=True)
for col in ['Close', 'SMA-50', 'SMA-200']:
    fig3.add_trace(go.Scatter(x=df.index, y=df[col], name=col), row=1, col=1)

fig3.data[0].name = 'Price'
add_volume_chart(fig3)
add_range_selector(fig3)
fig3.update_layout(xaxis=dict(rangeselector = dict(font = dict( color = 'black'))))
fig3.update_yaxes(title_text = 'Price', row=1, col=1)
fig3.update_yaxes(title_text = 'Volume', row=2, col=1)
set_padding(fig3)
fig3.update_xaxes(rangebreaks=[dict(values=dt_breaks)])
layout3 = go.Layout(template=TEMPLATE, title=TICKER + ' - Price, SMA-50, SMA-200 and Volume', height=500)
fig3.update_layout(layout3)

CandleStick Chart

In [34]:
fig4 = go.Figure(data=[go.Candlestick(x=df.index, open=df['Open'], high=df['High'], low=df['Low'], close=df['Close'])])
set_padding(fig4)
fig4.update_xaxes(rangebreaks=[dict(values=dt_breaks)])
fig4.update_layout(xaxis=dict(rangeselector = dict(font = dict( color = 'black'))))
fig4.update_yaxes(title_text='Price')
fig4.update_xaxes(title_text='Date')
fig4.update_layout(title = TICKER + ' - CandleStick Chart', xaxis_rangeslider_visible=False, height=500, template=TEMPLATE)

Plot RSI

In [35]:
df['RSI'] = ta.RSI(df.Close,14)

fig5 = make_subplots(rows=2,cols=1,vertical_spacing=0.01,shared_xaxes=True)
fig5.add_trace(go.Scatter(x=df.index,y=df['RSI'], name='RSI'), row=1, col=1)

fig5.add_hline(y=30, line_dash='dash', line_color='limegreen', line_width=1)
fig5.add_hline(y=70, line_dash='dash', line_color='red', line_width=1)
fig5.update_yaxes(title_text='RSI Score')

add_volume_chart(fig5)
add_range_selector(fig5)
fig5.update_layout(xaxis=dict(rangeselector = dict(font = dict( color = 'black'))))
set_padding(fig5)
fig5.update_xaxes(rangebreaks=[dict(values=dt_breaks)])

fig5['layout']['yaxis']['title']= 'RSI score'
fig5['layout']['yaxis2']['title']= 'Volume'
fig5['layout']['xaxis2']['title']= 'Date'

layout5 = go.Layout(template=TEMPLATE, title=TICKER + ' - RSI', height=500,
                    xaxis=dict(rangeselector = dict(font = dict( color = 'black'))))
fig5.update_layout(layout5)

Bollinger Bands

{'matype': {0: 'Simple Moving Average',
  1: 'Exponential Moving Average',
  2: 'Weighted Moving Average',
  3: 'Double Exponential Moving Average',
  4: 'Triple Exponential Moving Average',
  5: 'Triangular Moving Average',
  6: 'Kaufman Adaptive Moving Average',
  7: 'MESA Adaptive Moving Average',
  8: 'Triple Generalized Double Exponential Moving Average'}}

In [36]:
df['BU'], df['BM'], df['BL'] = ta.BBANDS(df.Close, timeperiod=20, matype=1)
fig6 = px.line(data_frame=df, x=df.index, y=['Close', 'BU', 'BM', 'BL'])

fig6.update_yaxes(title_text='Price')
fig6.update_xaxes(title_text='Date')
fig6.data[0].name='Price'
set_padding(fig6)

fig6.update_xaxes(
    rangeselector = dict(
                buttons = list([
                    dict(count = 1, label = '1m', step = 'month', stepmode = 'backward'),
                    dict(count = 6, label = '6m', step = 'month', stepmode = 'backward'),
                    dict(count = 1, label = 'YTD', step = 'year', stepmode = 'todate'),
                    dict(count = 1, label = '1y', step = 'year', stepmode = 'backward'),
                    dict(step = 'all')
                ])
    )
)

layout6 = go.Layout(template=TEMPLATE, title=TICKER + ' - Price, Bollinger Bands', height=500,
                    xaxis1=dict(rangeselector = dict(font = dict( color = 'black'))))
fig6.update_layout(layout6)

Add signals (buy and sell)

In [37]:
df_buy = df.query('Low < BL')[['Close']]
df_sell = df.query('High > BU')[['Close']]

df_buy['Close'] = df_buy['Close'].round(2)
df_sell['Close'] = df_sell['Close'].round(2)

Plot Buy and Sell Signals

In [43]:
fig7 = go.Figure(data=[go.Candlestick(x=df.index, open=df['Open'], high=df['High'], low=df['Low'],
    close=df['Close'], name='Candlestick')])

# Plot BU line graph; don't show legend
fig7.add_trace(go.Scatter(x=df.index, y=df['BU'], fill=None, mode='lines', showlegend=False))

# Plot BL line graph and fill upto BU; don't show legend
fig7.add_trace(go.Scatter(x=df.index, y=df['BL'], fill='tonexty', mode='lines', showlegend=False))

# Plot Buy signals
fig7.add_trace(go.Scatter(x=df_buy.index, y=df_buy['Close'], mode='markers',
    marker=dict(symbol='x', size=7, line=dict(width=1)), name = 'Buy'))

# Plot Sell Signals
fig7.add_trace(go.Scatter(x=df_sell.index, y=df_sell['Close'], mode='markers',
    marker=dict(symbol='diamond', size=7, line=dict(width=1)), name = 'Sell'))

# Update y  & x axis labels
fig7.update_yaxes(title_text='Price')
fig7.update_xaxes(title_text='Date')
    
# Change the Close to Price for the legend label
fig7.data[0].name = 'Price'

# Sets customized padding
set_padding(fig7)

fig7.update_xaxes(
    rangeselector=dict(
        buttons=list([
            dict(count=1, label='1m', step='month', stepmode='backward'),
            dict(count=6, label='6m', step='month', stepmode='backward'),
            dict(count=1, label='YTD', step='year', stepmode='todate'),
            dict(count=1, label='1y', step='year', stepmode='backward'),
            dict(step='all')
        ])
    )
)

# Make it pretty
layout7 = go.Layout(template=TEMPLATE, title=TICKER + ' - Buy / Sell Signals', height=500, xaxis_rangeslider_visible = False,
                    xaxis1=dict(rangeselector=dict(font=dict(color='black'))))
fig7.update_layout(layout7)

MACD

In [49]:
analysis = pd.DataFrame()
analysis['macd'],analysis['macdSignal'], analysis['macdHist'] = ta.MACD(df.Close, fastperiod=12, slowperiod=26, signalperiod=9)

fig8=make_subplots(rows=2,cols=1, vertical_spacing=0.25,shared_xaxes=True)
fig8.append_trace(go.Candlestick(x=df.index, open=df['Open'], high=df['High'], low=df['Low'],
                                      close=df['Close'],showlegend=False, name='Candlestick'), row=1,col=1)

fig8.append_trace(go.Scatter(x=df.index, y=analysis['macd'], line=dict(color='#C42836', width=1),
                             name='MACD Line'), row=2,col=1)

fig8.append_trace(go.Scatter(x=df.index, y=analysis['macdSignal'], line=dict(color='limegreen', width=1),
                             name='Signal Line'), row=2,col=1)

colors = np.where(analysis['macd'] < 0, '#EA071C', '#57F219')

fig8.append_trace(go.Bar(x=df.index, y=analysis['macdHist'], marker_color=colors,
                             name='Histogram'), row=2,col=1)

# Update y  & x axis labels
fig8.update_yaxes(title_text='Price')
fig8.update_xaxes(title_text='Date')
    
# Change the Close to Price for the legend label
fig8.data[0].name = 'Price'

# Sets customized padding
set_padding(fig8)

fig8.update_xaxes(
    rangeselector=dict(
        buttons=list([
            dict(count=1, label='1m', step='month', stepmode='backward'),
            dict(count=6, label='6m', step='month', stepmode='backward'),
            dict(count=1, label='YTD', step='year', stepmode='todate'),
            dict(count=1, label='1y', step='year', stepmode='backward'),
            dict(step='all')
        ])
    )
)

# Make it pretty
layout8 = go.Layout(template=TEMPLATE, title=TICKER + ' - MACD Indicator', height=700, xaxis_rangeslider_visible = False,
                    xaxis1=dict(rangeselector=dict(font=dict(color='black'))),
                    xaxis2=dict(rangeselector=dict(font=dict(color='black'))))
fig8.update_layout(layout8)
fig8.update_layout(legend=dict(yanchor='top',y=0.45,xanchor='left',x=1.01))
fig8.show()

Multiple Tickers

In [39]:
df_multi = yf.download(TICKERS,start = START)['Close']
df_multi

[*********************100%%**********************]  20 of 20 completed


ABBV        AMGN        AMZN          BA         CAT  \
Date                                                                     
2021-01-04  105.410004  226.660004  159.331497  202.720001  182.149994   
2021-01-05  106.500000  227.759995  160.925507  211.630005  183.639999   
2021-01-06  105.580002  233.250000  156.919006  211.029999  193.860001   
2021-01-07  106.709999  234.020004  158.108002  212.710007  194.229996   
2021-01-08  107.269997  238.490005  159.134995  209.899994  194.259995   
...                ...         ...         ...         ...         ...   
2023-12-18  153.419998  275.480011  154.070007  260.410004  285.709991   
2023-12-19  153.600006  278.440002  153.789993  263.510010  292.959991   
2023-12-20  151.690002  275.179993  152.119995  260.250000  289.709991   
2023-12-21  152.589996  279.329987  153.839996  262.019989  290.070007   
2023-12-22  154.940002  284.160004  153.419998  260.440002  290.359985   

                 CSCO         DIS          GS         IBM       INTC  \
Date                                                                   
2021-01-04  43.959999  177.679993  265.000000  118.489487  49.669998   
2021-01-05  43.980000  178.440002  270.929993  120.592735  50.610001   
2021-01-06  44.400002  179.119995  285.549988  123.604210  51.099998   
2021-01-07  44.959999  178.580002  291.649994  123.317398  52.189999   
2021-01-08  45.060001  178.690002  290.079987  122.877632  51.650002   
...               ...         ...         ...         ...        ...   
2023-12-18  50.240002   92.860001  376.399994  162.740005  45.689999   
2023-12-19  50.180000   93.930000  382.450012  161.559998  46.660000   
2023-12-20  49.799999   91.269997  377.519989  160.050003  45.759998   
2023-12-21  49.700001   92.019997  380.570007  160.779999  47.080002   
2023-12-22  50.090000   91.019997  380.649994  162.139999  48.000000   

                   JNJ         JPM         KO         LLY         MCD  \
Date                                                                    
2021-01-04  156.500000  125.870003  52.759998  165.500000  210.220001   
2021-01-05  158.339996  125.650002  52.180000  166.320007  211.479996   
2021-01-06  159.830002  131.550003  50.520000  164.320007  211.000000   
2021-01-07  160.369995  135.869995  49.959999  165.830002  211.979996   
2021-01-08  160.039993  136.020004  51.080002  166.410004  215.869995   
...                ...         ...        ...         ...         ...   
2023-12-18  155.440002  166.229996  59.020000  579.760010  290.230011   
2023-12-19  156.460007  168.449997  58.830002  579.809998  290.730011   
2023-12-20  153.270004  166.550003  57.610001  570.210022  288.989990   
2023-12-21  154.839996  167.500000  57.990002  572.000000  291.390015   
2023-12-22  155.460007  167.399994  58.320000  570.390015  291.700012   

                  PYPL        REGN        TSLA           V         WMT  
Date                                                                    
2021-01-04  231.919998  482.859985  243.256668  217.759995  146.529999  
2021-01-05  234.910004  483.450012  245.036667  214.509995  145.750000  
2021-01-06  226.830002  470.089996  251.993332  212.619995  146.660004  
2021-01-07  235.039993  481.200012  272.013336  213.809998  146.649994  
2021-01-08  242.460007  498.730011  293.339996  215.449997  146.630005  
...                ...         ...         ...         ...         ...  
2023-12-18   61.470001  850.869995  252.080002  258.369995  154.970001  
2023-12-19   63.009998  848.390015  257.220001  259.989990  155.529999  
2023-12-20   61.740002  841.789978  247.139999  257.109985  153.710007  
2023-12-21   62.060001  841.880005  254.500000  259.540009  154.800003  
2023-12-22   61.840000  846.719971  252.539993  258.429993  156.649994  

[749 rows x 20 columns]

Normalize the prices

In [40]:
df_multi = df_multi.fillna(df_multi.mean())

# Normalize the data
mean = np.mean(df_multi, axis=0)
std = np.std(df_multi, axis=0)
norm_df = (df_multi - mean) / std
norm_df

ABBV      AMGN      AMZN        BA       CAT      CSCO  \
Date                                                                     
2021-01-04 -1.684646 -0.816743  0.768314  0.064256 -1.444704 -1.420523   
2021-01-05 -1.625490 -0.759275  0.826280  0.337450 -1.390046 -1.416411   
2021-01-06 -1.675420 -0.472457  0.680583  0.319053 -1.015139 -1.330071   
2021-01-07 -1.614092 -0.432229  0.723821  0.370565 -1.001566 -1.214951   
2021-01-08 -1.583700 -0.198700  0.761168  0.284405 -1.000466 -1.194393   
...              ...       ...       ...       ...       ...       ...   
2023-12-18  0.920944  1.733793  0.576978  1.833118  2.354248 -0.129529   
2023-12-19  0.930713  1.888434  0.566796  1.928168  2.620204 -0.141864   
2023-12-20  0.827054  1.718119  0.506066  1.828212  2.500983 -0.219982   
2023-12-21  0.875898  1.934930  0.568614  1.882482  2.514189 -0.240538   
2023-12-22  1.003438  2.187268  0.553341  1.834037  2.524827 -0.160365   

                 DIS        GS       IBM      INTC       JNJ       JPM  \
Date                                                                     
2021-01-04  1.305743 -2.442256 -1.587757  0.599926 -1.231753 -1.041924   
2021-01-05  1.325648 -2.260717 -1.368690  0.681371 -0.996974 -1.055732   
2021-01-06  1.343457 -1.813146 -1.055026  0.723826 -0.806854 -0.685410   
2021-01-07  1.329315 -1.626402 -1.084899  0.818267 -0.737952 -0.414260   
2021-01-08  1.332196 -1.674466 -1.130704  0.771480 -0.780059 -0.404844   
...              ...       ...       ...       ...       ...       ...   
2023-12-18 -0.915692  0.968104  3.021215  0.255087 -1.367005  1.491330   
2023-12-19 -0.887668  1.153317  2.898310  0.339131 -1.236856  1.630671   
2023-12-20 -0.957334  1.002391  2.741035  0.261152 -1.643891  1.511415   
2023-12-21 -0.937691  1.095763  2.817068  0.375521 -1.443564  1.571043   
2023-12-22 -0.963881  1.098212  2.958721  0.455233 -1.364453  1.564766   

                  KO       LLY       MCD      PYPL      REGN      TSLA  \
Date                                                                     
2021-01-04 -1.399768 -1.411265 -2.014054  1.069622 -1.701846 -0.064865   
2021-01-05 -1.540309 -1.404256 -1.958047  1.104416 -1.696388 -0.032904   
2021-01-06 -1.942550 -1.421351 -1.979383  1.010392 -1.819972  0.092008   
2021-01-07 -2.078245 -1.408444 -1.935822  1.105928 -1.717201  0.451482   
2021-01-08 -1.806854 -1.403486 -1.762911  1.192271 -1.555044  0.834417   
...              ...       ...       ...       ...       ...       ...   
2023-12-18  0.117116  2.129785  1.542397 -0.913825  1.702342  0.093564   
2023-12-19  0.071077  2.130212  1.564622 -0.895905  1.679401  0.185857   
2023-12-20 -0.224546  2.048153  1.487278 -0.910683  1.618349  0.004863   
2023-12-21 -0.132467  2.063453  1.593960 -0.906960  1.619182  0.137017   
2023-12-22 -0.052504  2.049691  1.607739 -0.909520  1.663953  0.101824   

                   V       WMT  
Date                            
2021-01-04 -0.201698  0.228660  
2021-01-05 -0.401211  0.150986  
2021-01-06 -0.517235  0.241606  
2021-01-07 -0.444183  0.240609  
2021-01-08 -0.343506  0.238619  
...              ...       ...  
2023-12-18  2.291291  1.069135  
2023-12-19  2.390740  1.124900  
2023-12-20  2.213941  0.943661  
2023-12-21  2.363117  1.052206  
2023-12-22  2.294974  1.236432  

[749 rows x 20 columns]

Plotting Performance

In [41]:
fig10 = px.line(data_frame=norm_df, x=norm_df.index, y=TICKERS)
set_padding(fig10)
fig10.update_xaxes(
    rangeselector = dict(
                buttons = list([
                    dict(count = 1, label = '1m', step = 'month', stepmode = 'backward'),
                    dict(count = 6, label = '6m', step = 'month', stepmode = 'backward'),
                    dict(count = 1, label = 'YTD', step = 'year', stepmode = 'todate'),
                    dict(count = 1, label = '1y', step = 'year', stepmode = 'backward'),
                    dict(step = 'all')
                ])
    )
)

layout10 = go.Layout(template=TEMPLATE, title='Performance', height=500,
                    xaxis=dict(rangeselector = dict(font = dict( color = 'black'))))
fig10.update_layout(layout10)